<a href="https://colab.research.google.com/github/str1k/ThaiClassification/blob/master/Taxicap_Location_Entrophy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip uninstall rtree
!sudo apt install libspatialindex-dev
!pip install pandas fiona shapely pyproj rtree --quiet
!pip install geopandas --quiet
!pip install -U alphashape geopy osmnx folium alphashape descartes --quiet

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  libspatialindex-c4v5 libspatialindex4v5
The following NEW packages will be installed:
  libspatialindex-c4v5 libspatialindex-dev libspatialindex4v5
0 upgraded, 3 newly installed, 0 to remove and 40 not upgraded.
Need to get 555 kB of archives.
After this operation, 3,308 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libspatialindex4v5 amd64 1.8.5-5 [219 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libspatialindex-c4v5 amd64 1.8.5-5 [51.7 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libspatialindex-dev amd64 1.8.5-5 [285 kB]
Fetched 555 kB in 1s (658 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.

In [1]:
import geopandas
from geopandas import GeoSeries
from shapely.geometry import Polygon
import numpy as np
import pyproj
import os, sys
import ogr
from math import ceil
from geopandas import gpd 
import pandas as pd
import shapely.geometry
from google.colab import drive
from os import walk
import alphashape
from descartes import PolygonPatch
import folium
from geopy.geocoders import Nominatim
from ipywidgets import interact, fixed, widgets
import matplotlib.pyplot as plt
import networkx as nx
import osmnx as ox
from shapely import geometry

In [122]:
# https://pcjericks.github.io/py-gdalogr-cookbook/vector_layers.html#create-fishnet-grid
def squareGridPolygon(outputGridfn,xmin,xmax,ymin,ymax,gridHeight,gridWidth):

    # convert sys.argv to float
    xmin = float(xmin)
    xmax = float(xmax)
    ymin = float(ymin)
    ymax = float(ymax)
    gridWidth = float(gridWidth)
    gridHeight = float(gridHeight)

    # get rows
    rows = ceil((ymax-ymin)/gridHeight)
    # get columns
    cols = ceil((xmax-xmin)/gridWidth)

    # start grid cell envelope
    ringXleftOrigin = xmin
    ringXrightOrigin = xmin + gridWidth
    ringYtopOrigin = ymax
    ringYbottomOrigin = ymax-gridHeight

    # create output file
    outDriver = ogr.GetDriverByName('ESRI Shapefile')
    if os.path.exists(outputGridfn):
        os.remove(outputGridfn)
    outDataSource = outDriver.CreateDataSource(outputGridfn)
    outLayer = outDataSource.CreateLayer(outputGridfn,geom_type=ogr.wkbPolygon )
    featureDefn = outLayer.GetLayerDefn()

    # create grid cells
    countcols = 0
    while countcols < cols:
        countcols += 1

        # reset envelope for rows
        ringYtop = ringYtopOrigin
        ringYbottom =ringYbottomOrigin
        countrows = 0

        while countrows < rows:
            countrows += 1
            ring = ogr.Geometry(ogr.wkbLinearRing)
            ringXleftOrigin_ringYtop = to_original_transformer.transform(ringXleftOrigin,ringYtop)
            ringXrightOrigin_ringYtop = to_original_transformer.transform(ringXrightOrigin,ringYtop)
            ringXrightOrigin_ringYbottom = to_original_transformer.transform(ringXrightOrigin,ringYbottom)
            ringXleftOrigin_ringYbottom = to_original_transformer.transform(ringXleftOrigin,ringYbottom)
            ring.AddPoint( ringXleftOrigin_ringYtop[1],ringXleftOrigin_ringYtop[0])
            ring.AddPoint( ringXrightOrigin_ringYtop[1],ringXrightOrigin_ringYtop[0])
            ring.AddPoint( ringXrightOrigin_ringYbottom[1],ringXrightOrigin_ringYbottom[0])
            ring.AddPoint( ringXleftOrigin_ringYbottom[1],ringXleftOrigin_ringYbottom[0])
            ring.AddPoint( ringXleftOrigin_ringYtop[1],ringXleftOrigin_ringYtop[0])
            poly = ogr.Geometry(ogr.wkbPolygon)
            poly.AddGeometry(ring)

            # add new geom to layer
            outFeature = ogr.Feature(featureDefn)
            outFeature.SetGeometry(poly)
            outLayer.CreateFeature(outFeature)
            outFeature.Destroy

            # new envelope for next poly
            ringYtop = ringYtop - gridHeight
            ringYbottom = ringYbottom - gridHeight

        # new envelope for next poly
        ringXleftOrigin = ringXleftOrigin + gridWidth
        ringXrightOrigin = ringXrightOrigin + gridWidth

    # Close DataSources
    outDataSource.Destroy()

In [2]:
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


In [83]:
path_to_file = "/content/gdrive/MyDrive/Colab Notebooks/cabspottingdata/"

file_name = []
for (dirpath, dirnames, filenames) in walk(path_to_file):
    file_name.extend(filenames)
    break

In [84]:
li = []
for f in file_name:
  if f != "README":
    load_pdf = pd.read_csv(path_to_file+f,sep=" ", index_col=None, header=None)
    load_pdf.columns = ['Longitute','Latitude','occupacy','date']
    load_pdf['user'] = f.split(".")[0].split("_")[1]
    li.append(load_pdf)

all_data_pdf = pd.concat(li, axis=0, ignore_index=True)
all_data_pdf['date'] = pd.to_datetime(all_data_pdf['date'],unit='s')

In [85]:
min_lat_long = all_data_pdf.loc[:,'Longitute':'Latitude'].min()
max_lat_long = all_data_pdf.loc[:,'Longitute':'Latitude'].max()

In [86]:
min_lat_long
# This acctually point us into the sea

Longitute     32.86970
Latitude    -127.08143
dtype: float64

In [100]:
!ls /content/gdrive/MyDrive/'san francisco neiborhood'/planning_neighborhoods.shp

planning_neighborhoods.dbf  planning_neighborhoods.shp.xml
planning_neighborhoods.prj  planning_neighborhoods.shx
planning_neighborhoods.shp


In [101]:
# https://geodata.lib.berkeley.edu/catalog/ark28722-s75c8t
# use sanfrancisco neiborhood shape to scope down data within sanfrancisco, eliminating all data points out of sanfrancisco area
# this will also remove data point of traveling to other city
sanfran_outline = gpd.GeoDataFrame.from_file('/content/gdrive/MyDrive/san francisco neiborhood/planning_neighborhoods.shp') 

# In case of further analysis, we could use https://geodata.lib.berkeley.edu/catalog/ark28722-s70k6k which is address shape file to analyze pick up and drop off address of each taxi ride

In [102]:
# convert original CRS EPSG:2227 to EPSG:4326
sanfran_outline = sanfran_outline.to_crs(4326)

In [103]:
sanfran_outline

OBJECTID  ...                                           geometry
0          1  ...  POLYGON ((-122.51251 37.76386, -122.51255 37.7...
1          2  ...  POLYGON ((-122.50940 37.74527, -122.50940 37.7...
2          3  ...  POLYGON ((-122.51317 37.77505, -122.51317 37.7...
3          4  ...  POLYGON ((-122.48409 37.78791, -122.48366 37.7...
4          5  ...  POLYGON ((-122.47782 37.77287, -122.47959 37.7...
5          6  ...  POLYGON ((-122.47601 37.74868, -122.47721 37.7...
6          7  ...  POLYGON ((-122.43596 37.76904, -122.43685 37.7...
7          8  ...  POLYGON ((-122.46260 37.78904, -122.46092 37.7...
8          9  ...  POLYGON ((-122.44646 37.77581, -122.45464 37.7...
9         10  ...  POLYGON ((-122.42096 37.80897, -122.42094 37.8...
10        11  ...  POLYGON ((-122.42488 37.81080, -122.42485 37.8...
11        12  ...  POLYGON ((-122.40879 37.79016, -122.40879 37.7...
12        13  ...  MULTIPOLYGON (((-122.40881 37.79016, -122.4088...
13        14  ...  POLYGON ((-122.42195 37.78849, -122.41861 37.7...
14        15  ...  POLYGON ((-122.40716 37.79036, -122.40628 37.7...
15        16  ...  POLYGON ((-122.44670 37.79474, -122.44782 37.8...
16        17  ...  POLYGON ((-122.42221 37.77291, -122.42327 37.7...
17        18  ...  POLYGON ((-122.44683 37.78725, -122.44723 37.7...
18        19  ...  POLYGON ((-122.38933 37.79142, -122.38881 37.7...
19        20  ...  POLYGON ((-122.42476 37.74785, -122.42495 37.7...
20        21  ...  POLYGON ((-122.37996 37.75206, -122.37996 37.7...
21        22  ...  POLYGON ((-122.38486 37.76712, -122.38485 37.7...
22        23  ...  POLYGON ((-122.42826 37.73179, -122.42815 37.7...
23        24  ...  POLYGON ((-122.44082 37.71646, -122.43828 37.7...
24        25  ...  POLYGON ((-122.39498 37.70841, -122.39968 37.7...
25        26  ...  POLYGON ((-122.42085 37.70833, -122.42388 37.7...
26        27  ...  POLYGON ((-122.45912 37.70822, -122.45973 37.7...
27        28  ...  POLYGON ((-122.47105 37.70820, -122.47283 37.7...
28        29  ...  POLYGON ((-122.50854 37.73536, -122.50854 37.7...
29        30  ...  POLYGON ((-122.42418 37.74226, -122.42394 37.7...
30        31  ...  POLYGON ((-122.43553 37.74146, -122.43563 37.7...
31        32  ...  POLYGON ((-122.46142 37.75156, -122.46035 37.7...
32        33  ...  POLYGON ((-122.44644 37.76104, -122.44641 37.7...
33        34  ...  POLYGON ((-122.42558 37.75662, -122.42495 37.7...
34        35  ...  POLYGON ((-122.45428 37.70822, -122.45456 37.7...
35        36  ...  POLYGON ((-122.45252 37.72317, -122.45695 37.7...

[36 rows x 3 columns]

In [3]:
%config InlineBackend.figure_format = 'retina'
plt.rcParams['figure.figsize'] = (10, 10)

In [106]:
m = folium.Map(location=[37.760049, -122.441011], zoom_start=13)
for _, r in sanfran_outline.iterrows():
    #without simplifying the representation of each borough, the map might not be displayed
    #sim_geo = gpd.GeoSeries(r['geometry'])
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['OBJECTID']).add_to(geo_j)
    geo_j.add_to(m)
m

In [90]:
# Swap longitute and latitute coordinate provided by source to desire arragement
sanfran_outline_swap = gpd.GeoDataFrame(crs=4326,geometry=sanfran_outline.geometry.map(lambda polygon: shapely.ops.transform(lambda x, y: (y, x), polygon)))

In [108]:
# Create geometry point and
# Convert pandas dataframe to geopandas
points = [shapely.geometry.Point(xy) for xy in zip(all_data_pdf["Latitude"],all_data_pdf["Longitute"])]
all_data_geopdf = gpd.GeoDataFrame(all_data_pdf,crs=4326,geometry=points)

In [109]:
all_data_geopdf

Longitute   Latitude  ...      user                     geometry
0          37.78203 -122.42747  ...  acdiyito  POINT (-122.42747 37.78203)
1          37.78237 -122.42427  ...  acdiyito  POINT (-122.42427 37.78237)
2          37.78307 -122.41941  ...  acdiyito  POINT (-122.41941 37.78307)
3          37.78357 -122.41602  ...  acdiyito  POINT (-122.41602 37.78357)
4          37.78362 -122.41565  ...  acdiyito  POINT (-122.41565 37.78362)
...             ...        ...  ...       ...                          ...
11220053   37.75619 -122.40277  ...    mfeuer  POINT (-122.40277 37.75619)
11220054   37.75431 -122.40628  ...    mfeuer  POINT (-122.40628 37.75431)
11220055   37.75307 -122.40642  ...    mfeuer  POINT (-122.40642 37.75307)
11220056   37.74839 -122.40825  ...    mfeuer  POINT (-122.40825 37.74839)
11220057   37.74828 -122.41356  ...    mfeuer  POINT (-122.41356 37.74828)

[11220058 rows x 6 columns]

In [114]:
sanfran_outline_swap

geometry
0  MULTIPOLYGON (((37.623 -122.630, 37.897 -122.6...

In [115]:
sanfran_points = gpd.sjoin(all_data_geopdf, sanfran_outline, op='within') 

In [117]:
sanfran_points = sanfran_points.drop(columns=['index_right'])

In [118]:
sanfran_points

Longitute   Latitude  ...  OBJECTID        NEIGHBORHO
0          37.78203 -122.42747  ...        17  Western Addition
1          37.78237 -122.42427  ...        17  Western Addition
146        37.77162 -122.42384  ...        17  Western Addition
159        37.76962 -122.43495  ...        17  Western Addition
160        37.77258 -122.43433  ...        17  Western Addition
...             ...        ...  ...       ...               ...
11198235   37.71205 -122.43772  ...        26    Crocker Amazon
11198236   37.71210 -122.43770  ...        26    Crocker Amazon
11201402   37.71276 -122.43156  ...        26    Crocker Amazon
11210505   37.71119 -122.44631  ...        26    Crocker Amazon
11219546   37.71122 -122.44675  ...        26    Crocker Amazon

[9881689 rows x 8 columns]

In [130]:
sanfran_outline


In [140]:
# We create boundary over sanfrancisco area and transform them in to EPSG:3857 for metric scaling
to_proxy_transformer = pyproj.Transformer.from_crs('epsg:4326', 'epsg:3857')
to_original_transformer = pyproj.Transformer.from_crs('epsg:3857', 'epsg:4326')
bondary = sanfran_outline['geometry'].bounds
se = to_proxy_transformer.transform( bondary['miny'].min(),bondary["minx"].min())
nw = to_proxy_transformer.transform( bondary['maxy'].max(),bondary['maxx'].max())

In [141]:
# Create Grid shape over sanfrancisco for location reference
# Square shape size of 100x100m will be created all over sanfrancisco area as location references (for computational wise i choose this number)
# Smaller size of grid could make location more precise in exchange with larger data points (Accuracy of GPRS should also be consider)
# Shape file will be create for further use
#
# In reality, we would be using prepared location-based polygon instead of this one, but in some case grid-based polygon also being use when precise location -
# is not available, and needed to be calculate based on reference point (Telecommunication way to get customer's location from CDR)
squareW = 100
squareW_ilustrate = 1000
path_to_square_grid_polygon = 'sfSquareGrid.shp'
path_to_square_grid_polygon_ill = 'sfSquareGrid_ill.shp'
squareGridPolygon(path_to_square_grid_polygon,se[0], nw[0],se[1],nw[1],squareW,squareW)
squareGridPolygon(path_to_square_grid_polygon_ill,se[0], nw[0],se[1],nw[1],squareW_ilustrate,squareW_ilustrate)

In [142]:
# Load square grid
sq_grid = gpd.GeoDataFrame.from_file(path_to_square_grid_polygon)
sq_grid_ill = gpd.GeoDataFrame.from_file(path_to_square_grid_polygon_ill)
sq_grid_ill

FID                                           geometry
0      0  POLYGON ((-122.51495 37.81157, -122.50596 37.8...
1      1  POLYGON ((-122.51495 37.80448, -122.50596 37.8...
2      2  POLYGON ((-122.51495 37.79738, -122.50596 37.7...
3      3  POLYGON ((-122.51495 37.79028, -122.50596 37.7...
4      4  POLYGON ((-122.51495 37.78318, -122.50596 37.7...
..   ...                                                ...
265  265  POLYGON ((-122.36223 37.74057, -122.35325 37.7...
266  266  POLYGON ((-122.36223 37.73347, -122.35325 37.7...
267  267  POLYGON ((-122.36223 37.72636, -122.35325 37.7...
268  268  POLYGON ((-122.36223 37.71926, -122.35325 37.7...
269  269  POLYGON ((-122.36223 37.71215, -122.35325 37.7...

[270 rows x 2 columns]

In [144]:
# Illustration of how square location grid look like (example of 1KM square grid)
# This will be use for illutration only since making smaller polygon grid mean more objects to draw and would cause out of memory issue
m = folium.Map(location=[37.760049, -122.441011], zoom_start=13)
for _, r in sq_grid_ill.iterrows():
    #without simplifying the representation of each borough, the map might not be displayed
    #sim_geo = gpd.GeoSeries(r['geometry'])
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['FID']).add_to(geo_j)
    geo_j.add_to(m)
m

In [149]:
del sq_grid_ill

In [146]:
# Mapping footfall point to grid location
sq_grid_location_based = gpd.sjoin(sanfran_points, sq_grid, op='within') 

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: EPSG:4326
Right CRS: None

  


In [147]:
# As we can see from this display output
# from user acdiyito index 0 and user abjoolaw index 22323 they where on coor 37.78203, -122.42747 and 37.78180, -112.42734
# If we were to calculate location entrophy on Lat Long coordinate this would resulting in marking them at two difference location
# However, as we create Geometry Polygon, we could recognize them both on the same Location grid of FID 14203

# From here, as we can also see in the displayed data, since this is driver footfall location, record are location stamp of their ride
# So, we need to remove some records within same Location grid
sq_grid_location_based

Longitute   Latitude  occupacy  ...        NEIGHBORHO index_right    FID
0          37.78203 -122.42747         0  ...  Western Addition       14203  14203
22323      37.78180 -122.42734         0  ...  Western Addition       14203  14203
29457      37.78183 -122.42738         1  ...  Western Addition       14203  14203
30053      37.78201 -122.42781         1  ...  Western Addition       14203  14203
35237      37.78210 -122.42730         1  ...  Western Addition       14203  14203
...             ...        ...       ...  ...               ...         ...    ...
11071850   37.70949 -122.44454         0  ...    Crocker Amazon       11531  11531
8864021    37.70929 -122.42625         1  ...    Crocker Amazon       14452  14452
8864022    37.70929 -122.42629         1  ...    Crocker Amazon       14452  14452
8864023    37.70929 -122.42629         0  ...    Crocker Amazon       14452  14452
10635755   37.70834 -122.44727         0  ...    Crocker Amazon       11095  11095

[9881689 rows x 10 columns]

In [150]:
# Save to gdrive
sq_grid_location_based.to_file("/content/gdrive/MyDrive/sq_grid_location_based.geojson", driver='GeoJSON')

In [4]:
sq_grid_location_based = gpd.GeoDataFrame.from_file("/content/gdrive/MyDrive/sq_grid_location_based.geojson")

In [15]:
del sq_grid_location_based

In [5]:
location_pdf = pd.DataFrame(sq_grid_location_based)

In [17]:
del location_pdf['geometry']
del location_pdf['index_right']

In [24]:
location_pdf['date'] = pd.to_datetime(location_pdf['date'],)

In [25]:
# We Then group by user, geometry location grid id, and windowed time of 15 mins (In assumption that car should be move to other location with some traffic) 
cleaned_location = (location_pdf.groupby( [location_pdf.date.dt.hour.mul(60).add(location_pdf.date.dt.minute) // 15, location_pdf.user,location_pdf.FID ], as_index=False).max()).sort_values('user')

In [188]:
user_visit_location = cleaned_location.groupby(['FID', 'user']).size().to_frame(name = 'userVisit').reset_index()

In [143]:
location_count_visit = cleaned_location.groupby("FID").size().to_frame(name = 'totalVisit').reset_index()

In [189]:
output= pd.merge(user_visit_location, location_count_visit, left_on='FID', right_on='FID', how='inner')

In [194]:
output['userProb'] = output['userVisit']/output['totalVisit']

In [196]:
output['entropy'] = -1*(output['userProb']*np.log(output['userProb'])/np.log(2))

In [197]:
del output['userVisit']
del output['userProb']
del output['totalVisit']

In [207]:
location_entropy_pdf= output.groupby(['user','FID']).sum().sort_values('entropy').reset_index()

In [208]:
location_entropy_pdf

user    FID   entropy
0          inquay  20562  0.000000
1        umhenwed   5366  0.000000
2        ocshitcl  21257  0.000000
3        otswrank  11225  0.000000
4         oafhynu  10908  0.000000
...           ...    ...       ...
2048143  ubnankke  20250  0.530702
2048144  avglybic  17652  0.530702
2048145  ellimtbu  19259  0.530713
2048146   onghoji   5762  0.530726
2048147    oshyon  18384  0.530730

[2048148 rows x 3 columns]

In [209]:
location_entropy_pdf.loc[location_entropy_pdf['user'] == 'oshyon']

user    FID   entropy
354      oshyon   6460  0.000000
10982    oshyon  14800  0.003704
12750    oshyon  19461  0.003896
24026    oshyon  17727  0.004643
35940    oshyon  19758  0.005310
...         ...    ...       ...
2044066  oshyon   6845  0.500000
2044099  oshyon   8928  0.500000
2046794  oshyon  22890  0.528321
2047028  oshyon   2262  0.528321
2048147  oshyon  18384  0.530730

[4668 rows x 3 columns]

In [224]:
example = location_entropy_pdf.loc[location_entropy_pdf['user'] == 'oshyon']

In [ ]:
sq_grid_pdf = pd.DataFrame(sq_grid)

In [225]:
example = pd.merge(example, sq_grid_pdf, left_on='FID', right_on='FID', how='inner')

In [226]:
example

user  ...                                           geometry
0     oshyon  ...  POLYGON ((-122.47542 37.78602, -122.47452 37.7...
1     oshyon  ...  POLYGON ((-122.42422 37.77324, -122.42332 37.7...
2     oshyon  ...  POLYGON ((-122.39547 37.78105, -122.39457 37.7...
3     oshyon  ...  POLYGON ((-122.40625 37.76827, -122.40535 37.7...
4     oshyon  ...  POLYGON ((-122.39368 37.77750, -122.39278 37.7...
...      ...  ...                                                ...
4663  oshyon  ...  POLYGON ((-122.47363 37.71997, -122.47273 37.7...
4664  oshyon  ...  POLYGON ((-122.46015 37.79596, -122.45925 37.7...
4665  oshyon  ...  POLYGON ((-122.37481 37.73062, -122.37391 37.7...
4666  oshyon  ...  POLYGON ((-122.50147 37.76046, -122.50057 37.7...
4667  oshyon  ...  POLYGON ((-122.40266 37.71641, -122.40176 37.7...

[4668 rows x 4 columns]

In [228]:
example_gdf = geopandas.GeoDataFrame(example, geometry=example['geometry'])

In [296]:

conditions = [
    (example_gdf['entropy'] <= 0.1),
    (example_gdf['entropy'] > 0.1) & (example_gdf['entropy'] <= 0.3),
    (example_gdf['entropy'] > 0.3) & (example_gdf['entropy'] <= 0.5),
    (example_gdf['entropy'] > 0.5) ]
choices = ['#E1C65A',  '#EB7F2C','#FF6633','#E50404']
example_gdf['RGBA'] = np.select(conditions, choices, default='#E1C65A')

In [293]:
example_gdf

user    FID  ...                                           geometry     RGBA
0     oshyon   6460  ...  POLYGON ((-122.47542 37.78602, -122.47452 37.7...  #FFFFFF
1     oshyon  14800  ...  POLYGON ((-122.42422 37.77324, -122.42332 37.7...  #FFFFFF
2     oshyon  19461  ...  POLYGON ((-122.39547 37.78105, -122.39457 37.7...  #FFFFFF
3     oshyon  17727  ...  POLYGON ((-122.40625 37.76827, -122.40535 37.7...  #FFFFFF
4     oshyon  19758  ...  POLYGON ((-122.39368 37.77750, -122.39278 37.7...  #FFFFFF
...      ...    ...  ...                                                ...      ...
4663  oshyon   6845  ...  POLYGON ((-122.47363 37.71997, -122.47273 37.7...  #E65A1D
4664  oshyon   8928  ...  POLYGON ((-122.46015 37.79596, -122.45925 37.7...  #E65A1D
4665  oshyon  22890  ...  POLYGON ((-122.37481 37.73062, -122.37391 37.7...  #F31010
4666  oshyon   2262  ...  POLYGON ((-122.50147 37.76046, -122.50057 37.7...  #F31010
4667  oshyon  18384  ...  POLYGON ((-122.40266 37.71641, -122.40176 37.7...  #F31010

[4668 rows x 5 columns]

In [297]:
# From here we can plot user's location entropy on map, and see the location according to their entropy
# Where red spot indicated higher entropy of user on the location
maploc = folium.Map(location=[37.760049, -122.441011],zoom_start=13,tiles="Stamen Toner")
example_gdf.crs = "epsg:4326"
folium.GeoJson(
    example_gdf,
    style_function=lambda feature: {
        'fillColor': feature['properties']['RGBA'],
        'color' : feature['properties']['RGBA'],
        'weight' : 0.8,
        'fillOpacity' : 0.6,
        }
    ).add_to(maploc)
maploc